In [1]:
import pandas as pd
import geopandas as gpd
import folium
import geopy
from geopy.distance import geodesic
from shapely.geometry import Point
import branca.colormap as cm
from ipywidgets import interact_manual, widgets, VBox, HBox
import ipywidgets as widgets
from sklearn.preprocessing import MinMaxScaler


In [2]:
# distritos = gpd.read_file("./SIRGAS_SHP_distrito/SIRGAS_SHP_distrito.shp")
# populacao = pd.read_csv("./Agregados_por_CEP_CNEFE_Censo_2022/Agregados_por_CEP_CNEFE_Censo_2022.csv", sep = ";" )
estacoes = pd.read_parquet("estacoes_reestruturadas.parquet")
declividade = gpd.read_file("./declividade/sad6996_declividade.shp")
### Ocorrencias eh criterios fisicos
# ocorrencias = gpd.read_file("./ocorrencias/SIRGAS_SHP_riscoocorrencia_2024.shp")

# Funções de Estações

In [3]:
## Prepara o dataframe de estações para as outras análises
## Retorna o dataframe tratado
def tratar_df_estacoes(df_estacoes):
    ## Cria uma geometria "Point"
    df_estacoes = gpd.GeoDataFrame(df_estacoes, geometry = gpd.points_from_xy(df_estacoes['lon'], df_estacoes['lat']))
    ## Define crs
    df_estacoes = df_estacoes.set_crs("EPSG:4326")
    return df_estacoes

## Cria circles (geometry Polygon) em volta de cada estação (geometry Point)
## Retorna o dataframe com a geometria "circles"
def criar_circulos_estacao(data, radius_km):
    circles = []
    for _, row in data.iterrows():
        circle_points = []
        center = (row['lat'], row['lon'])
        ## Dizemos que é aproximadamente um círculo, pois é um polígono regular com 360 vértices
        for angle in range(0,360, 1): 
            destination = geopy.distance.distance(kilometers = radius_km).destination(center, angle)
            circle_points.append(Point(destination.longitude, destination.latitude))
        circle = gpd.GeoSeries(circle_points).unary_union.convex_hull
        circles.append(circle)
    data.rename(columns = {'geometry':'point'}, inplace = True)
    circles_gdf = gpd.GeoDataFrame(data, geometry = circles)
    circles_gdf.rename(columns = {'geometry':'circle'}, inplace = True)
    return circles_gdf

## Adiciona os círculos no mapa, usa como base a função "criar_circulos_estacao"
## Retorna o Mapa com os círculos (geometry polygon) e pontos (geometry point) adicionados
def adicionar_estacoes_com_circulos_mapa(mapa, df_estacoes, radius_km):
    ## Definição dos layers para controle do usuário por camadas
    layer_estacoes =  folium.FeatureGroup(name = "Estações")
    layer_circulos_estacoes = folium.FeatureGroup(name = f"Redondezas {radius_km} km") 
    ## Se o df_estacoes já tem os circles, não precisa criá-los
    if "circle" not in df_estacoes:
        data = criar_circulos_estacao(df_estacoes, radius_km)
    else:
        data = df_estacoes.copy()
    ## Define "circle" como geometria a ser usada, pois há mais de uma em uso
    data.set_geometry("circle", inplace = True)
    ## Adiciona Circlemarkers ao layer
    for _, row in data.iterrows():
        folium.CircleMarker(
                    location=[row['lat'],row['lon']],
                    color = "blue",
                    radius= 5,
                    tooltip= row['name'],
                    fill=True,
                    fill_opacity=1,
                    fill_color="blue",
                ).add_to(layer_estacoes)
    ## Adiciona os Circles ao layer
    for _, row in data.iterrows():
        folium.GeoJson(
            row['circle'].__geo_interface__, 
            tooltip = row['name'],
            style_function=lambda x:{'fillColor': 'gray', 'color': 'gray', 'fillOpacity': 0.0},
        ).add_to(layer_circulos_estacoes)
        layer_estacoes.add_to(mapa)
        layer_circulos_estacoes.add_to(mapa)
        folium.LayerControl().add_to(mapa)
    return mapa

# Funções de Mapa

In [4]:
## Define cores para mapas
def get_color(valor):
    if valor == 1:
        return "yellow"
    elif valor == 2:
        return "orange"
    elif valor == 3:
        return "red"
    elif valor == 4:
        return "darkred"
    else:
        return "black" # error

## Cria um mapa centrado em São Paulo
def criar_mapa_sp():
    mapa_sp = folium.Map(location = [-23.550520, -46.633308], zoom_start = 12)
    return mapa_sp

## Plota Circlemarkers de 1 cor, dado 1 df com Lat e Lon
def plot_circlemarkers_one_color(data, color, radius, name, pontuacao, layer):
    for _, row in data.iterrows():
        folium.CircleMarker(
                location = [row['lat'], row['lon']],
                color = color, 
                radius = radius,
                tooltip = row[name] + " " + str(row[pontuacao]), 
                popup = row[name] + " " + str(row[pontuacao]), 
                fill = True,
                fill_opacity = 1,
                fill_color = color,
        ).add_to(layer)

## Plota Circlemarkers de várias cores, dado 1 df com Lat e Lon e um Colormap branca
def plot_circlemarkers_multi_color(data, radius, name, pontuacao, layer, colormap):
    for _, row in data.iterrows():
        folium.CircleMarker(
                location = [row['lat'], row['lon']],
                color = colormap(row[pontuacao]), 
                radius = radius,
                tooltip = row[name] + " " + str(row[pontuacao]), 
                popup =  row[name] + " " + str(row[pontuacao]), 
                fill = True,
                fill_opacity = 1,
                fill_color = colormap(row[pontuacao]),
        ).add_to(layer)
        
    


# Função de Identificação de Outliers



In [5]:
## Plota os Circlemarkers outliers dado um out_lower, out_upper e non_outliers, separados pela função "identificar_outliers"
def plot_circlemarkers_outliers(out_lower, out_upper, non_outliers, color_lower, color_upper, radius, 
                                name, pontuacao, layer, colormap):
    plot_circlemarkers_one_color(out_lower, color_lower, radius, name, pontuacao, layer)
    plot_circlemarkers_one_color(out_upper, color_upper, radius, name, pontuacao, layer)
    plot_circlemarkers_multi_color(non_outliers, radius, name, pontuacao, layer, colormap)

def identificar_outliers(df, coluna):
    """
    Identifica outliers em uma coluna de um DataFrame usando o método IQR.

    Parâmetros:
        df (pd.DataFrame): DataFrame contendo os dados.
        coluna (str): Nome da coluna para identificar os outliers.

    Retorna:
        outliers_lower (pd.DataFrame): DataFrame contendo os outliers inferiores.
        outliers_upper (pd.DataFrame): DataFrame contendo os outliers superiores.
        non_outliers (pd.DataFrame): DataFrame contendo os dados não-outliers.
    """
    Q1 = df[coluna].quantile(0.25) 
    Q3 = df[coluna].quantile(0.75)
    IQR = Q3 - Q1
    lowerbound = Q1 - 1.5 * IQR
    upperbound = Q3 + 1.5 * IQR

    outliers_lower = df[df[coluna] < lowerbound]
    outliers_upper = df[df[coluna] > upperbound]
    non_outliers = df[(df[coluna] >= lowerbound) & (df[coluna] <= upperbound)]

    return outliers_lower, outliers_upper, non_outliers 


# Funções de Declividade

In [12]:
## Prepara o dataframe de declividade para análise
def tratar_df_declividade(df_declividade):
    df_declividade = df_declividade.set_crs("EPSG:29183")  # Define o CRS, se ainda não estiver definido
    df_declividade = df_declividade.to_crs("EPSG:4326")   # Converte para WGS84 (latitude/longitude)
    substituicoes = {
        '0 a 05%': 1,
        '05 a 25%': 2,
        '25 a 60%': 3,
        '> 60%': 4
    }

    # Substituindo valores
    df_declividade['CLASSE'] = df_declividade['CLASSE'].replace(substituicoes).astype(int)
    return df_declividade

## Faz a análise da declividade 
def analise_declividade(df_estacoes, df_declividade, radius_km):
   ## Cria mapa a ser usado
    mapa = criar_mapa_sp()
    ## Cria círculos em volta da estação (de 1 km ou a quantidade que definir) e seta geometria como circle
    df_estacoes_circulo = criar_circulos_estacao(df_estacoes, radius_km)
    df_estacoes_circulo.set_geometry("circle", inplace=True)  
    ## Une as estações e a declividade fazendo a "intersecção"
    cruzamentos =  gpd.sjoin(df_estacoes_circulo, df_declividade, how="inner", predicate="intersects")
    
    cruzamentos_finais = cruzamentos[[
        "name",  # Nome da estação
        "circle",  # Geometria 'circle' da estação
        "point",  # Geometria 'point' da estação
        "ID",     # ID da declividade
        "AREA",   # Área do distrito
        "CLASSE", # Código do distrito
    ]].copy()

    ## Inclui a coluna da geometria da declividade no cruzamentos finais
    # cruzamentos_finais["district_geometry"] = df_declividade.loc[cruzamentos["index_right"], "geometry"].values
    cruzamentos_finais = cruzamentos_finais.merge(
        df_declividade[["ID", "geometry"]],  # Apenas as colunas relevantes
        on="ID",  # A coluna para equivalência
        how="left"  # Tipo de junção (left mantém todos os dados de cruzamentos)
    )
    declividade_necessaria_para_plot = cruzamentos_finais.copy()

    ## Sistema de pontuação específico
    cruzamentos_finais['intersection'] =  cruzamentos_finais.apply(lambda row: 
            (row['circle'].intersection(row['geometry'])).area * (row['CLASSE'] * 25) if not row['circle'].intersection(row['geometry']).is_empty 
                                                                                               else 0, axis=1)
    ## Criação de Layers para mapa
    layer_declividade = folium.FeatureGroup(name = "Declividade")
    layer_estacoes =  folium.FeatureGroup(name = "Estações")
    layer_circulos_estacoes = folium.FeatureGroup(name = f"Redondezas {radius_km} km") 

    ## Cruzamentos_finais serve apenas para plotar a declividade
    declividade_necessaria_para_plot = cruzamentos_finais.drop_duplicates(subset='geometry')
    ## Plot da Declividade
    for _, row in declividade_necessaria_para_plot.iterrows():
        cor = get_color(row['CLASSE'])
        geo_json = row['geometry'].__geo_interface__
        folium.GeoJson(
            geo_json, 
            tooltip = str(row['ID']) + " Classe " + str(row['CLASSE']),
            style_function = lambda x, color = cor:{'fillColor' : color , 'color' : color, 'weight' : 1}
        ).add_to(layer_declividade)
          
    cruzamentos_finais = cruzamentos_finais.groupby('name', as_index = False)['intersection'].mean()
    cruzamentos_finais= pd.merge(cruzamentos_finais, df_estacoes_circulo, on = 'name',  how = 'left')
    out_lower, out_upper, non_outliers = identificar_outliers(cruzamentos_finais, "intersection")
    scaler = MinMaxScaler()
    non_outliers['intersection'] = scaler.fit_transform(non_outliers[['intersection']])
    colormap = cm.linear.plasma.scale(non_outliers['intersection'].min(), 
                                      non_outliers['intersection'].max())
    colormap.add_to(mapa)

    plot_circlemarkers_outliers(out_lower, out_upper, non_outliers, "black", "green", 5, 
                                "name", "intersection", layer_estacoes, colormap)    

    ## Plota círculos em volta das estações
    for _, row in df_estacoes_circulo.iterrows():    
        folium.GeoJson(
            row['circle'].__geo_interface__, 
            tooltip = row['name'],
            style_function=lambda x:{'fillColor': 'gray', 'color': 'gray', 'fillOpacity': 0.0},
        ).add_to(layer_circulos_estacoes)
        
    layer_declividade.add_to(mapa)
    layer_estacoes.add_to(mapa)
    layer_circulos_estacoes.add_to(mapa)
    folium.LayerControl().add_to(mapa)

    return mapa
    

In [7]:
estacoes = tratar_df_estacoes(estacoes)
declividade = tratar_df_declividade(declividade)


C:\Users\gabia\AppData\Local\Temp\ipykernel_768\4099071580.py:13: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_declividade['CLASSE'] = df_declividade['CLASSE'].replace(substituicoes).astype(int)


In [13]:
analise_declividade(estacoes,declividade, 0.5)

C:\Users\gabia\AppData\Local\Temp\ipykernel_768\2202293004.py:24: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:4326

  cruzamentos =  gpd.sjoin(df_estacoes_circulo, df_declividade, how="inner", predicate="intersects")
C:\Users\gabia\AppData\Local\Temp\ipykernel_768\2202293004.py:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  non_outliers['intersection'] = scaler.fit_transform(non_outliers[['intersection']])
